# **Create AwA2 dataset for Hugging Face...**

The aim is to achieve a consistent dataset format for use in machine vision and for Hugging Face.

## **Load and Imports libraries**

In [21]:
!apt install git-lfs

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
git-lfs is already the newest version (3.0.2-1ubuntu0.3).
0 upgraded, 0 newly installed, 0 to remove and 38 not upgraded.


In [22]:
print("\n",100*"#","\n")
%pip show polars
print("\n",100*"#","\n")
%pip show pandas
print("\n",100*"#","\n")
%pip show numpy
print("\n",100*"#","\n")
%pip show matplotlib
print("\n",100*"#","\n")
%pip show huggingface_hub
print("\n",100*"#","\n")
%pip show datasets
print("\n",100*"#","\n")
%pip show pyarrow
print("\n",100*"#","\n")
%pip show pillow
print("\n",100*"#","\n")
%pip show opencv-python
print("\n",100*"#","\n")


 #################################################################################################### 

Name: polars
Version: 1.21.0
Summary: Blazingly fast DataFrame library
Home-page: https://www.pola.rs/
Author: 
Author-email: Ritchie Vink <ritchie46@gmail.com>
License: 
Location: /usr/local/lib/python3.11/dist-packages
Requires: 
Required-by: cudf-polars-cu12
Note: you may need to restart the kernel to use updated packages.

 #################################################################################################### 

Name: pandas
Version: 2.2.3
Summary: Powerful data structures for data analysis, time series, and statistics
Home-page: https://pandas.pydata.org
Author: 
Author-email: The Pandas Development Team <pandas-dev@python.org>
License: BSD 3-Clause License

Copyright (c) 2008-2011, AQR Capital Management, LLC, Lambda Foundry, Inc. and PyData Development Team
All rights reserved.

Copyright (c) 2011-2023, Open source contributors.

Redistribution and use in source 

In [23]:
import zipfile
import os, sys
import shutil
import json
import random
import subprocess
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import polars as pl
import pyarrow as pa
import cv2
import pickle

import pyarrow.parquet as pq

from PIL import Image

from kaggle_secrets import UserSecretsClient

from datasets import Dataset, DatasetDict

from huggingface_hub import (
    Repository, 
    get_full_repo_name,
    login,
    upload_folder,
    hf_hub_download,
    HfApi
)

## **Support functions**

In [24]:
def save_pickle(input_save, file_path):
    try:
        with open(file_path, "wb") as outfile:
            pickle.dump(input_save, outfile)
            print(f"File: {file_path} was saved.")
    except Exception as err:
        print(f"Save file: {file_path} false!\n", err)

In [25]:
def load_pickle(file_path):
    try:
        with open(file_path, "rb") as infile:
         	record_obj = pickle.load(infile)
        return record_obj
    except Exception as err:
        print(f"Load file: {file_path} false!\n", err)

In [26]:
def load_text_file(file_path):
    try:
        with open(file_path, "r") as file:
            content = file.read()
        return content
    except Exception as err:
        print(f"Load file: {file_path} false!\n", err)

In [27]:
def save_text_file(text_save, file_path):
    try:
        with open(file_path, "a") as f:
            f.write(text_save)
            print(f"File: {file_path} was saved.")
    except Exception as err:
        print(f"Save file: {file_path} false!\n", err)

In [28]:
def load_json_file(file_path):
    try:
        with open(file_path, 'r') as file:
            data = json.load(file)
        return data
    except Exception as err:
        print(f"Load file: {file_path} false!\n", err)

In [29]:
def save_json_file(input_data, file_path):
    try:
        with open(file_path, "w") as f:
            json.dump(input_data, f, indent=4)
            print(f"File: {file_path} was saved.")
    except Exception as err:
        print(f"Save file: {file_path} false!\n", err)
    

In [30]:
def list_files_dir(path_dir):
    files_dist = {}
    
    file_names = os.listdir(path_dir)
    
    for file_name in file_names:
        name = file_name.split('.')[0]
        path = os.path.join(path_dir, file_name)
        files_dist[name] = path
    
    return files_dist

In [31]:
def list_dir_in_dir(path_dir):
    directories = [name for name in os.listdir(path_dir) if os.path.isdir(os.path.join(path_dir, name))]
    return directories

## **Load data**

#### ***Path of directories***

In [32]:
path_pose_data = os.path.join('/kaggle','input','awa2-dataset','AwA2','pose','Annotations')
path_images = os.path.join('/kaggle','input','awa2-dataset','AwA2','data','JPEGImages')
path_license_image = os.path.join('/kaggle','input','awa2-dataset','AwA2','data','licenses')

#### ***Names of directories of files***

#### *Images:*

In [33]:
list_dir_images = list_dir_in_dir(path_images)
list_dir_images_sort = sorted(list_dir_images)
print(f"Number of images of directories is {len(list_dir_images_sort)}")
print('\n', list_dir_images_sort)

Number of images of directories is 50

 ['antelope', 'bat', 'beaver', 'blue+whale', 'bobcat', 'buffalo', 'chihuahua', 'chimpanzee', 'collie', 'cow', 'dalmatian', 'deer', 'dolphin', 'elephant', 'fox', 'german+shepherd', 'giant+panda', 'giraffe', 'gorilla', 'grizzly+bear', 'hamster', 'hippopotamus', 'horse', 'humpback+whale', 'killer+whale', 'leopard', 'lion', 'mole', 'moose', 'mouse', 'otter', 'ox', 'persian+cat', 'pig', 'polar+bear', 'rabbit', 'raccoon', 'rat', 'rhinoceros', 'seal', 'sheep', 'siamese+cat', 'skunk', 'spider+monkey', 'squirrel', 'tiger', 'walrus', 'weasel', 'wolf', 'zebra']


#### *licence of images:*

In [34]:
list_dir_licenses = list_dir_in_dir(path_license_image)
list_dir_licenses_sort = sorted(list_dir_licenses)
print(f"Number of licenses of directories is {len(list_dir_licenses_sort)}")
print('\n', list_dir_licenses_sort)

Number of licenses of directories is 50

 ['antelope', 'bat', 'beaver', 'blue+whale', 'bobcat', 'buffalo', 'chihuahua', 'chimpanzee', 'collie', 'cow', 'dalmatian', 'deer', 'dolphin', 'elephant', 'fox', 'german+shepherd', 'giant+panda', 'giraffe', 'gorilla', 'grizzly+bear', 'hamster', 'hippopotamus', 'horse', 'humpback+whale', 'killer+whale', 'leopard', 'lion', 'mole', 'moose', 'mouse', 'otter', 'ox', 'persian+cat', 'pig', 'polar+bear', 'rabbit', 'raccoon', 'rat', 'rhinoceros', 'seal', 'sheep', 'siamese+cat', 'skunk', 'spider+monkey', 'squirrel', 'tiger', 'walrus', 'weasel', 'wolf', 'zebra']


#### *pose data:*

In [35]:
list_dir_pose_data = list_dir_in_dir(path_pose_data)
list_dir_pose_data_sort = sorted(list_dir_pose_data)
print(f"Number of licenses of directories is {len(list_dir_pose_data_sort)}")
print('\n', list_dir_pose_data_sort)

Number of licenses of directories is 37

 ['antelope', 'bobcat', 'buffalo', 'chihuahua', 'collie', 'cow', 'dalmatian', 'deer', 'elephant', 'fox', 'german+shepherd', 'giant+panda', 'giraffe', 'grizzly+bear', 'hippopotamus', 'horse', 'leopard', 'lion', 'moose', 'otter', 'ox', 'persian+cat', 'pig', 'polar+bear', 'rabbit', 'raccoon', 'rat', 'rhinoceros', 'sample', 'sheep', 'siamese+cat', 'skunk', 'squirrel', 'tiger', 'weasel', 'wolf', 'zebra']


> Note: At first glance, it is clear that the image dataset and their positions are not identical.

#### *Check class*

In [36]:
print(list_dir_licenses_sort==list_dir_images_sort)
print(list_dir_licenses_sort==list_dir_pose_data_sort and list_dir_pose_data_sort==list_dir_images_sort)

True
False


## **Create dataframe of pose annotation**

In [37]:
total_dataset_list = []

In [ ]:
%%time
for directory in list_dir_pose_data_sort:
    path = os.path.join(path_pose_data, directory)
    data_list = list_files_dir(path)
    for data_path in data_list:
        path_input = os.path.join(path_pose_data, directory, data_path + '.pickle')
        data = load_pickle(path_input)
        data_input = data['a1']
        data_input['name_file'] = data_path
        data_input['name_class'] = directory
        total_dataset_list.append(data_input)
       
        

{'right_eye': [359.57142857142856, 658.4285714285714], 'right_earbase': [285.8571428571429, 634.4285714285714], 'right_earend': [96.14285714285717, 520.1428571428571], 'right_antler_base': [363.0, 563.0], 'right_antler_end': [67.0, 92.71428571428571], 'left_antler_base': [453.8571428571429, 539.5714285714286], 'left_antler_end': [296.71428571428567, 82.42857142857143], 'left_earbase': [407.0, 539.0], 'left_earend': [423.0, 467.57142857142856], 'left_eye': [508.1428571428571, 635.5714285714286], 'nose': [544.1428571428571, 796.7142857142857], 'upper_jaw': [550.4285714285714, 821.2857142857143], 'lower_jaw': [541.8571428571429, 840.7142857142857], 'mouth_end_right': [488.1428571428571, 831.0], 'throat_base': [453.28571428571433, 865.2857142857143], 'neck_base': [290.42857142857144, 696.1428571428571], 'neck_end': [265.8571428571429, 869.2857142857143], 'back_base': [253.28571428571433, 871.0], 'back_middle': [107.57142857142856, 824.7142857142857], 'back_end': [32.71428571428572, 785.857

In [41]:
total_dataset_list

[{'right_eye': [359.57142857142856, 658.4285714285714],
  'right_earbase': [285.8571428571429, 634.4285714285714],
  'right_earend': [96.14285714285717, 520.1428571428571],
  'right_antler_base': [363.0, 563.0],
  'right_antler_end': [67.0, 92.71428571428571],
  'left_antler_base': [453.8571428571429, 539.5714285714286],
  'left_antler_end': [296.71428571428567, 82.42857142857143],
  'left_earbase': [407.0, 539.0],
  'left_earend': [423.0, 467.57142857142856],
  'left_eye': [508.1428571428571, 635.5714285714286],
  'nose': [544.1428571428571, 796.7142857142857],
  'upper_jaw': [550.4285714285714, 821.2857142857143],
  'lower_jaw': [541.8571428571429, 840.7142857142857],
  'mouth_end_right': [488.1428571428571, 831.0],
  'throat_base': [453.28571428571433, 865.2857142857143],
  'neck_base': [290.42857142857144, 696.1428571428571],
  'neck_end': [265.8571428571429, 869.2857142857143],
  'back_base': [253.28571428571433, 871.0],
  'back_middle': [107.57142857142856, 824.7142857142857],
  

In [46]:
df_keypoints_data = pd.DataFrame(total_dataset_list)
df_polars_keypoints_data = pl.from_pandas(df_keypoints_data)

In [47]:
df_polars_keypoints_data.head(100)

shape: (100, 69)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ right_eye ┆ right_ear ┆ right_ear ┆ right_ant ┆ … ┆ left_ey   ┆ throat_be ┆ tail_be   ┆ back_lef │
│ ---       ┆ base      ┆ end       ┆ ler_base  ┆   ┆ ---       ┆ ---       ┆ ---       ┆ t_ta     │
│ list[f64] ┆ ---       ┆ ---       ┆ ---       ┆   ┆ list[f64] ┆ list[f64] ┆ list[f64] ┆ ---      │
│           ┆ list[f64] ┆ list[f64] ┆ list[f64] ┆   ┆           ┆           ┆           ┆ list[f64 │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ ]        │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ [359.5714 ┆ [285.8571 ┆ [96.14285 ┆ [363.0,   ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ 29, 658.4 ┆ 43, 634.4 ┆ 7, 520.14 ┆ 563.0]    ┆   ┆           ┆           ┆           ┆          │
│ 28571]    ┆ 28571]    ┆ 2857]     ┆           ┆   ┆           ┆           ┆           ┆          │
│ [799.4545 ┆ [769.9090 ┆ [790.3636 ┆ [-1.0,    ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ 45, 213.7 ┆ 91, 195.5 ┆ 36, 158.7 ┆ -1.0]     ┆   ┆           ┆           ┆           ┆          │
│ 27273]    ┆ 45455]    ┆ 27273]    ┆           ┆   ┆           ┆           ┆           ┆          │
│ [-1.0,    ┆ [447.1818 ┆ [433.5454 ┆ [-1.0,    ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ -1.0]     ┆ 18, 291.9 ┆ 55, 252.3 ┆ -1.0]     ┆   ┆           ┆           ┆           ┆          │
│           ┆ 09091]    ┆ 63636]    ┆           ┆   ┆           ┆           ┆           ┆          │
│ [566.2583 ┆ [553.8181 ┆ [500.7081 ┆ [577.7416 ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ 73, 247.3 ┆ 82, 225.3 ┆ 34, 189.9 ┆ 27, 209.0 ┆   ┆           ┆           ┆           ┆          │
│ 25359]    ┆ 15789]    ┆ 09091]    ┆ 47847]    ┆   ┆           ┆           ┆           ┆          │
│ [380.1428 ┆ [286.4285 ┆ [141.2857 ┆ [354.4285 ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ 57, 220.1 ┆ 71, 190.4 ┆ 14, 58.42 ┆ 71, 168.1 ┆   ┆           ┆           ┆           ┆          │
│ 42857]    ┆ 28571]    ┆ 8571]     ┆ 42857]    ┆   ┆           ┆           ┆           ┆          │
│ …         ┆ …         ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ [592.1818 ┆ [584.4545 ┆ [502.1818 ┆ [604.0,   ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ 18, 325.9 ┆ 45, 297.2 ┆ 18, 244.0 ┆ 278.63636 ┆   ┆           ┆           ┆           ┆          │
│ 09091]    ┆ 72727]    ┆ 90909]    ┆ 4]        ┆   ┆           ┆           ┆           ┆          │
│ [361.8571 ┆ [351.5714 ┆ [330.4285 ┆ [375.0,   ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ 43, 381.8 ┆ 29, 356.7 ┆ 71,       ┆ 341.28571 ┆   ┆           ┆           ┆           ┆          │
│ 57143]    ┆ 14286]    ┆ 315.0]    ┆ 4]        ┆   ┆           ┆           ┆           ┆          │
│ [439.0,   ┆ [437.1818 ┆ [406.2727 ┆ [449.0,   ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ 295.27272 ┆ 18, 289.8 ┆ 27, 271.1 ┆ 279.36363 ┆   ┆           ┆           ┆           ┆          │
│ 7]        ┆ 18182]    ┆ 81818]    ┆ 6]        ┆   ┆           ┆           ┆           ┆          │
│ [456.2727 ┆ [447.1818 ┆ [107.1818 ┆ [516.7272 ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ 27, 333.2 ┆ 18,       ┆ 18, 242.8 ┆ 73, 221.9 ┆   ┆           ┆           ┆           ┆          │
│ 72727]    ┆ 281.0]    ┆ 18182]    ┆ 09091]    ┆   ┆           ┆           ┆           ┆          │
│ [-1.0,    ┆ [-1.0,    ┆ [554.9090 ┆ [517.6363 ┆ … ┆ null      ┆ null      ┆ null      ┆ null     │
│ -1.0]     ┆ -1.0]     ┆ 91, 252.5 ┆ 64, 268.9 ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ 45455]    ┆ 09091]    ┆   ┆           ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [50]:
columns = df_polars_keypoints_data.columns
columns

['right_eye',
 'right_earbase',
 'right_earend',
 'right_antler_base',
 'right_antler_end',
 'left_antler_base',
 'left_antler_end',
 'left_earbase',
 'left_earend',
 'left_eye',
 'nose',
 'upper_jaw',
 'lower_jaw',
 'mouth_end_right',
 'throat_base',
 'neck_base',
 'neck_end',
 'back_base',
 'back_middle',
 'back_end',
 'tail_base',
 'body_middle_right',
 'bbox',
 'mouth_end_left',
 'throat_end',
 'tail_end',
 'front_left_thai',
 'front_left_knee',
 'front_left_paw',
 'front_right_thai',
 'front_right_paw',
 'front_right_knee',
 'back_left_knee',
 'back_left_paw',
 'back_left_thai',
 'back_right_thai',
 'back_right_paw',
 'back_right_knee',
 'belly_bottom',
 'body_middle_left',
 'name_file',
 'name_class',
 'left_antlerbase',
 'left_antlerend',
 'right_antlerend',
 'right_antlerbase',
 'neckbase',
 'neckend',
 'backbase',
 'backmiddle',
 'backend',
 'tailend',
 'bellybottom',
 'back_right_pi',
 'tail_e',
 'left_eara',
 'right_earE',
 'right_earea',
 'left_ear_base',
 'left_ear_end',
 